# RESULTS ANALYSIS OF THE  REVERBERATION EXPERIMENT

In [85]:
import os
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from scipy.stats import norm, chi2_contingency
import math
from pychoacoustics import pysdt
import numpy as np
import pingouin as pg
import pingouin as pg

Z = norm.ppf
pd.set_option('display.max_rows', 100)
pd.set_option('display.max_colwidth', None)

bin_h = 60
fv_h = 200
wro_h = 0
cor_h = 120

base_s = 60
base_v = 75
base_a = 1

alpha = .05

## Read Data

In [2]:
results_folder = 'test_dataframes'
exp_data = pd.read_csv(os.path.join(results_folder, 'experiment.csv'))
preliminary_data = pd.read_csv(os.path.join(results_folder, 'preliminary.csv'))
subject_data = pd.read_csv(os.path.join(results_folder, 'subject_info.csv'))

## Preprocess data

In [3]:
n_trials_tot = exp_data.shape[0]
complexities = list(np.sort(exp_data['complexity'].unique()))
rooms = list(exp_data['room'].unique())

# Add impostor gender
# exp_data.loc[(exp_data['speaker_impostor'] == 'DAVID') | (exp_data['speaker_impostor'] == 'ALEX'),'impostor_sex'] = 'M'
# exp_data.loc[(exp_data['speaker_impostor'] == 'MARIA') | (exp_data['speaker_impostor'] == 'SUSAN'),'impostor_sex'] = 'F'

# 'impostor_correct_answer' = NaN when subject answered 'Yes, they are all in the same room'
exp_data_imp_adj = exp_data.copy(deep=True)
exp_data_imp_adj.loc[exp_data_imp_adj.same_room_answer == 'Yes', 'impostor_correct_answer'] = float('nan')

## Subjects Data

In [ ]:
subject_data

In [ ]:
fig = px.histogram(subject_data, x="sex", title='Sex distribution')
fig.show()

fig = px.histogram(subject_data, x="age", title='Age range distribution')
fig.show()

fig = px.histogram(subject_data, x="reverberation", title='Experience on reverberation distribution')
fig.show()

fig = px.histogram(subject_data, x="vr", title='Experience on VR distribution')
fig.show()

fig = px.histogram(subject_data, x="impairment", title='Hearing impairment distribution')
fig.show()

fig = px.histogram(subject_data, x="duration", title='Experiment duration distribution')
fig.show()

## Preliminary Experiment

In [5]:
def plot_preliminary(df):
    groups_names = ['condition', 'room', 'speaker']

    for group_name in groups_names:
        fig = go.Figure()

        trace = go.Histogram(histnorm='percent')
        trace.name = 'Overall'
        trace.x = df['externalization']
        fig.add_trace(trace)

        for name, group in df.groupby(group_name):
            trace = go.Histogram(histnorm='percent')
            trace.name = name
            trace.x = group['externalization']
            fig.add_trace(trace)

        fig.update_layout(
            title_text=group_name.upper(),
            yaxis_title_text='%')
        fig.update_xaxes(categoryorder='array', categoryarray= ['Inside', 'Edge', 'Outside'])
        fig.show()

### Preliminary Experiment -  Overall

Remove the first 3 trials of the preliminary experiment for each subject (hidden training)

In [6]:
preliminary_data_filt = preliminary_data[preliminary_data['trial_id_per_subject'] > 3]

In [7]:
# preliminary_data_filt['condition'].replace({'Ref': 'None', 'HOA_Bin': 'Bin', 'FV': 'Freeverb'}, inplace=True)

In [ ]:
plot_preliminary(preliminary_data_filt)

### Preliminary Experiment -  Males

Keep only males (the greater group)

In [ ]:
preliminary_data_filt_male = preliminary_data_filt[
    preliminary_data_filt.subject_progressive_id.isin(subject_data[subject_data.sex=='Male'].subject_progressive_id)]

In [ ]:
plot_preliminary(preliminary_data_filt_male)

## Experiment Results

### Accuracies with bar plots

In [ ]:
exp_data

In [108]:
def plot_accuracies(res_df, groups_names):
    fig = go.Figure(data=[go.Bar(name='Yes', x=['Yes'],
                                 y=[(exp_data['same_room_answer'] == 'Yes').sum()/exp_data['same_room_answer'].count()]),
                          go.Bar(name='No', x=['No'],
                                 y=[(exp_data['same_room_answer'] == 'No').sum()/exp_data['same_room_answer'].count()])
                         ],
                    layout_yaxis_range=[0, 1]
                   )
    fig.update_layout(barmode='stack',
                     title_text='Percentage of Yes and No answers',
                     yaxis_title_text='%')
    fig.show()
    
    acc_names = ['Accuracy same room', 'Accuracy impostor']
    acc_cols = ['same_correct_answer', 'impostor_correct_answer']
    n_rows = res_df.shape[0]

    overall_bar = go.Bar(name='OVERALL', x=acc_names, y=[res_df[acc].sum()/res_df[acc].count() for acc in acc_cols])
    fig = go.Figure([overall_bar], layout_yaxis_range=[0, 1]) 

    fig.update_layout(
        title_text='Overall Accuracies',
        yaxis_title_text='%')
    fig.show()

    for group_name in groups_names:
        bar_data = [overall_bar]

        for name, group in res_df.groupby(group_name):
            bar_data.append(go.Bar(name=name, x=acc_names, y=[group[acc].sum()/group[acc].count() for acc in acc_cols]))
            
        fig = go.Figure(data=bar_data, layout_yaxis_range=[0, 1])

        fig.update_layout(
            title_text=group_name.upper(),
            yaxis_title_text='%')
        fig.show()
        
        # Sub conditions
        
        # Iterate on the fields different from the current field
        for group_sub in groups_names:
            if group_sub != group_name:
                
                group_sub_values = res_df[group_sub].unique()
                # Iterate on the values of the current field
                for group_val in group_sub_values:
                    
                    res_df_filt = res_df[res_df[group_sub] == group_val]
                    
                    overall_bar_sub = go.Bar(name=f"[{group_val}]OVERALL", x=acc_names, y=[res_df_filt[acc].sum()/res_df_filt[acc].count() for acc in acc_cols])
                    bar_data = [overall_bar_sub]

                    for name, group in res_df_filt.groupby(group_name):
                        bar_data.append(go.Bar(name=f"[{group_val}]{name}", x=acc_names, y=[group[acc].sum()/group[acc].count() for acc in acc_cols]))

                    fig = go.Figure(data=bar_data, layout_yaxis_range=[0, 1])

                    fig.update_layout(
                        title_text=f"[{group_sub.upper()}: {group_val}] {group_name.upper()}",
                        yaxis_title_text='%')
                    fig.show()

chi-squared or Fisher's exact test to assess difference between conditions? ANOVA should be used for continuous data, here we have binary data.

Accuracies plots having `impostor_correct_answer` = NaN when subject answered ''Yes, they are all in the same room''

In [109]:
plot_accuracies(exp_data_imp_adj, ['condition', 'room', 'complexity', 'speaker_impostor'])

Accuracies plots having `impostor_correct_answer` = `same_correct_answer` when subject answered ''Yes, they are all in the same room'' (for STD analysis)

In [110]:
plot_accuracies(exp_data, ['condition', 'room', 'complexity', 'speaker_impostor'])

#### Statistical analysis

In [111]:
expected, observed, stats = pg.chi2_independence(exp_data_imp_adj, x='condition', y='same_correct_answer')

In [112]:
expected

same_correct_answer           0           1
condition                                  
Freeverb             117.666667  161.333333
HOA_Bin              117.666667  161.333333
NONE                 117.666667  161.333333

In [113]:
observed

same_correct_answer    0    1
condition                    
Freeverb             106  173
HOA_Bin              127  152
NONE                 120  159

In [114]:
stats

test    lambda      chi2  dof      pval    cramer     power
0             pearson  1.000000  3.360698  2.0  0.186309  0.063365  0.355854
1        cressie-read  0.666667  3.364397  2.0  0.185965  0.063400  0.356204
2      log-likelihood  0.000000  3.373066  2.0  0.185160  0.063482  0.357024
3       freeman-tukey -0.500000  3.380691  2.0  0.184456  0.063554  0.357745
4  mod-log-likelihood -1.000000  3.389290  2.0  0.183664  0.063634  0.358558
5              neyman -2.000000  3.409462  2.0  0.181821  0.063823  0.360463

### Analysis per subject

In [115]:
def overall_analysis(y_bin, y_fv, paired, chance_lvl=0.5, alpha=.05):
    res_bin = pg.normality(y_bin, alpha=alpha)
    print(f'Normality Bin: {res_bin.normal.values[0]}')

    res_fv = pg.normality(y_fv, alpha=alpha)
    print(f'Normality Freeverb: {res_fv.normal.values[0]}')
            
    
    if res_bin.normal.values[0] & res_fv.normal.values[0]:
        print('\nt-test')
        
        res_bin_fv = pg.ttest(y_bin, y_fv, paired=paired)

        res_bin_chn = pg.ttest(y_bin, chance_lvl)

        res_fv_chn = pg.ttest(y_fv, chance_lvl)

    else:
        print('\nWilcoxon')
        
        if paired:
            res_bin_fv = pg.wilcoxon(y_bin, y_fv)
        else:
            res_bin_fv = pg.mwu(y_bin, y_fv)

        res_bin_chn = pg.wilcoxon(y_bin - chance_lvl)

        res_fv_chn = pg.wilcoxon(y_fv - chance_lvl)
            
        
    print('\nBin == Freeverb' if res_bin_fv['p-val'][0] > alpha else '\nBin != Freeverb')
    print(res_bin_fv)
    
    print(f'\nBin == {chance_lvl}' if res_bin_chn['p-val'][0] > alpha else f'\nBin != {chance_lvl}')
    print(res_bin_chn)
    
    print(f'\nFreeverb == {chance_lvl}' if res_fv_chn['p-val'][0] > alpha else f'\nFreeverb != {chance_lvl}')
    print(res_fv_chn)
    

def plot_violin_subj(exp_data, res_col, analysis=[], paired=None, title=''):
    
    fig = go.Figure(layout_yaxis_range=[0, 1])
    
    pointpos_bin = [-0.8,-0.8,-0.8,-0.8]
    pointpos_fv = [0.8,0.8,0.8,0.8]
    
    df_bin = exp_data.copy(deep=True)
    df_bin = exp_data[exp_data['condition'] != 'Freeverb']
    df_fv = exp_data.copy(deep=True)
    df_fv = exp_data[exp_data['condition'] != 'HOA_Bin']

    
    overall_dist_bin = df_bin.groupby(['subject_progressive_id'])[res_col].mean()
    complexity_dists_bin = df_bin.groupby(['subject_progressive_id', 'complexity'])[res_col].mean()
    overall_dist_fv = df_fv.groupby(['subject_progressive_id'])[res_col].mean()
    complexity_dists_fv = df_fv.groupby(['subject_progressive_id', 'complexity'])[res_col].mean()
    
    x_names = ['Overall'] + sorted(exp_data['complexity'].unique().tolist())

    for i, x_name in enumerate(x_names):
        if x_name == 'Overall':
            y_bin = overall_dist_bin
            y_fv = overall_dist_fv

            if 'overall' in analysis:
                print('\nSTATISTICAL ANALYSIS - OVERALL')
                overall_analysis(y_bin, y_fv, paired, chance_lvl=0.5)
        
        else:
            y_bin = complexity_dists_bin.loc[:, x_name]
            y_fv = complexity_dists_fv.loc[:, x_name]
            
            
            if 'complexity' in analysis:
                print(f'\nSTATISTICAL ANALYSIS - COMPLEXITY {x_name}')
                overall_analysis(y_bin, y_fv, paired, chance_lvl=1/x_name)


            
        fig.add_trace(go.Violin(x=[x_name] * overall_dist_bin.shape[0],
                                y=y_bin,
                                name='Bin',
                                legendgroup='Bin',
                                scalegroup='Bin',
                                side='negative',
                                line_color=f'hsva({bin_h}, {base_s}, {base_v}, {base_a})',
                                showlegend=x_name == 'Overall',
                                pointpos=pointpos_bin[i],
#                                 points='all',
#                                 jitter=0.5
                               )
                     )

        fig.add_trace(go.Violin(x=[x_name] * overall_dist_fv.shape[0],
                                y=y_fv,
                                name='Freeverb',
                                legendgroup='Freeverb',
                                scalegroup='Freeverb',
                                side='positive',
                                line_color=f'hsva({fv_h}, {base_s}, {base_v}, {base_a})',
                                showlegend=x_name == 'Overall',
                                pointpos=pointpos_fv[i],
#                                 points='all',
#                                 jitter=0.5
                               )
                     )
        
    fig.update_traces(box_visible=True, meanline_visible=True,
                      points='all',
                      jitter=0.3,
                      marker_size=5,
                      line_width=1.1
                     )
    fig.update_layout(violingap=0,
                      violingroupgap=0.3,
                      violinmode='overlay',
                      title_text=title,            
                      yaxis_range=[-0.02,1.02],
                      xaxis_title='Complexity',
                      yaxis_title='Accuracy [%]',
                      legend_title='Condition'
                     )
    fig.show()

#### Detection

In [116]:
plot_violin_subj(exp_data_imp_adj,
                 'same_correct_answer',
                 analysis=['overall'],
                 paired=True,
                 title='Detection of Bin and Freeverb per complexity')


STATISTICAL ANALYSIS - OVERALL
Normality Bin: True
Normality Freeverb: True

t-test

Bin == Freeverb
               T  dof alternative     p-val          CI95%   cohen-d   BF10  \
T-test -1.660542   30   two-sided  0.107224  [-0.08, 0.01]  0.265926  0.654   

           power  
T-test  0.299579  

Bin != 0.5
              T  dof alternative     p-val        CI95%   cohen-d   BF10  \
T-test  2.46592   30   two-sided  0.019604  [0.51, 0.6]  0.442892  2.532   

           power  
T-test  0.665115  

Freeverb != 0.5
               T  dof alternative     p-val         CI95%  cohen-d    BF10  \
T-test  3.465212   30   two-sided  0.001619  [0.54, 0.65]  0.62237  21.477   

           power  
T-test  0.918092  


#### Identification

All trials

wrong detection                 -> wrong identification

correct detection (No impostor) -> correct identification

In [117]:
plot_violin_subj(exp_data,
                 'impostor_correct_answer',
                 analysis=[],
                 paired=None,
                 title='Identification of Bin and Freeverb per complexity')

Ignore trials with detection answers ''No impostor'' (identification task not performed)

wrong detection -> wrong identification

In [118]:
plot_violin_subj(exp_data_imp_adj,
                 'impostor_correct_answer',
                 analysis=[],
                 paired=None,
                 title='Identification of Bin and Freeverb per complexity')

Ignore trials of wrong detection

correct detection (No impostor) -> correct identification

In [119]:
plot_violin_subj(exp_data[exp_data['same_correct_answer'] == 1],
                 'impostor_correct_answer',
                 analysis=[],
                 paired=None,
                 title='Identification of Bin and Freeverb per complexity')

Consider only trials of correct impostor detection

(Ignore trials of wrong detection and correct detection of No impostor)

Come si comporta il soggetto nell'identification quando passa correttamente la detection? Si considerano quindi solo i trial dove la identification ha effettivamente senso (detection True Positive). Se risponde Negative alla detection non ha senso l'identification dato che non risponde alla domanda "Chi non è nella stessa stanza?" sia che faccia giusto (True Negative) che sbagliato (False Negative). Se risponde Positive alla detection e sbaglia (False Positive) non può rispondere giusto alla domanda "Chi non è nella stessa stanza?"

In [120]:
plot_violin_subj(exp_data[(exp_data['same_correct_answer'] == 1) & (exp_data['condition'] != 'NONE')],
                 'impostor_correct_answer',
                 analysis=['overall','complexity'],
                 paired=False,
                 title='Identification of Bin and Freeverb per complexity')


STATISTICAL ANALYSIS - OVERALL
Normality Bin: False
Normality Freeverb: True

Wilcoxon

Bin == Freeverb
     U-val alternative     p-val       RBC      CLES
MWU  389.0   two-sided  0.198198  0.190427  0.404787

Bin == 0.5
          W-val alternative     p-val       RBC  CLES
Wilcoxon  136.0   two-sided  0.128991 -0.330049   NaN

Freeverb == 0.5
          W-val alternative     p-val   RBC  CLES
Wilcoxon  142.5   two-sided  0.841249  0.05   NaN

STATISTICAL ANALYSIS - COMPLEXITY 2
Normality Bin: False
Normality Freeverb: False

Wilcoxon

Bin == Freeverb
     U-val alternative     p-val       RBC      CLES
MWU  426.0   two-sided  0.928632 -0.014286  0.507143

Bin == 0.5
          W-val alternative     p-val       RBC  CLES
Wilcoxon  159.0   two-sided  0.660665  0.094017   NaN

Freeverb == 0.5
          W-val alternative     p-val       RBC  CLES
Wilcoxon  100.0   two-sided  0.577534  0.134199   NaN

STATISTICAL ANALYSIS - COMPLEXITY 3
Normality Bin: False
Normality Freeverb: False

Wilco

A che domanda rispondono questi grafici? Quale domanda ci interessa di più?

### Alluvial plot

In [121]:
trg_val = ['Yes', 'No']
trg_lbl = ['Noise', 'Signal']

In [122]:
def generate_alluvial(src_idx, trg_idx, link_vals, link_lbls, link_cols, labels, cols, x_pos, y_pos, pad=10):
    sank = go.Sankey(
    arrangement='snap',
    valueformat = ".2f",
    valuesuffix = "%",
    # Define nodes
    node = dict(
        pad = pad,
        thickness = 10,
        line = dict(color = "black", width = 0.5),
        label =  labels,
        color =  cols,
        x = x_pos,
        y = y_pos,
    ),
    # Add links
    link = dict(
      source =  src_idx,
      target =  trg_idx,
      value =  link_vals,
      label =  link_lbls,
      color =  link_cols
    ))
    
    return sank
    
    
    
def plot_alluvial(df,
                  src_col,
                  trg_col,
                  title='Alluvial plot',
                  percentage=True,
                  return_fig=False,
                  identification_col=None,
                  impostor_sex_col=None,
                  save_to=None):
    n_trials_tot = df.shape[0]
    

    
    if impostor_sex_col is None:
        src_vals = ['NONE', 'HOA_Bin', 'Freeverb']
        src_lbls = ['Real', 'Bin', 'Freeverb']
        trg_vals = ['Yes', 'No']
        trg_lbls = ['Noise', 'Signal']
        labels = src_lbls + trg_lbls

        src_idx = [0, 0, 1, 1, 2, 2]
        trg_idx = [3, 4, 3, 4, 3, 4]
        link_lbls = ['True Negative', 'False Positive', 'False Negative', 'True Positive', 'False Negative', 'True Positive']
        link_vals = [((df[src_col] == src_vals[src_idx[n]]) & (df[trg_col] == trg_vals[trg_idx[n] - len(src_vals)])).sum()
                    for n in range(len(src_idx))]

    else:
        src_vals = ['NONE', 'HOA_Bin', 'Freeverb']
        src_vals_nodes = ['NONE', 'HOA_Bin', 'HOA_Bin', 'Freeverb', 'Freeverb']
        src_sex_vals = ['M', 'F']
        src_sec_vals_nodes = ['', 'M', 'F', 'M', 'F']
        src_lbls = ['None', 'Bin(M)', 'Bin(F)', 'Freeverb(M)', 'Freeverb(F)']
        trg_vals = ['Yes', 'No']
        trg_lbls = ['Noise', 'Signal']
        labels = src_lbls + trg_lbls

        src_idx = [0, 0, 1, 1, 2, 2, 3, 3, 4, 4]
        trg_idx = [5, 6, 5, 6, 5, 6, 5, 6, 5, 6]
        link_lbls = ['True Negative', 'False Positive',
                     'False Negative', 'True Positive', 'False Negative', 'True Positive',
                     'False Negative', 'True Positive', 'False Negative', 'True Positive']
#         link_vals = [((df[src_col] == src_vals[src_idx[n]]) & (df[trg_col] == trg_vals[trg_idx[n] - len(src_vals)])).sum()
#                      if src_vals[src_idx[n]] == 'NONE' else
#                      ((df[src_col] == src_vals[src_idx[n]]) & (df[trg_col] == trg_vals[trg_idx[n] - len(src_vals)]) &
#                       (df[impostor_sex_col] == src_sex_val[n % len(src_sex_val)])).sum()
#                      for n in range(len(src_idx))]
        link_vals = []
        for n in range(len(src_idx)):
            if src_vals_nodes[src_idx[n]] == 'NONE':
                a=((df[src_col] == src_vals_nodes[src_idx[n]]) & (df[trg_col] == trg_vals[trg_idx[n] - max(src_idx)-1])).sum()
            else:
                a=((df[src_col] == src_vals_nodes[src_idx[n]]) & (df[trg_col] == trg_vals[trg_idx[n] - max(src_idx)-1]) &
                              (df[impostor_sex_col] == src_sec_vals_nodes[src_idx[n]])).sum()
            link_vals.append(a)
        
        
    
    # COLORS
    op = 0.35
    step = 15
    sex_step = 20

    hues = [0, bin_h, fv_h]
    saturations = [0, base_s, base_s]
    values = [25, base_v, base_v]
    cols = []
    link_cols = []
    
    for c in range(len(src_vals)):
        cols.append(f'hsva({hues[c]}, {saturations[c]}, {values[c]+step}, {op})')
        
        col = f'hsva({hues[c]}, {saturations[c]}, {values[c]}, {op})'
        link_cols.append(col)
        link_cols.append(col)
        
        if (c > 0) & (impostor_sex_col is not None):
            cols.append(f'hsva({hues[c]+sex_step}, {saturations[c]}, {values[c]+step}, {op})')
            
            col = f'hsva({hues[c]+sex_step}, {saturations[c]}, {values[c]}, {op})'
            link_cols.append(col)
            link_cols.append(col)
        
    cols = cols + [cols[0], f'hsva(0, 0, 100, {op})']
            
    if percentage:
        link_vals = [v / n_trials_tot for v in link_vals]
        
    
    trg_node_pos_noise = sum([link_vals[i] for i, t in enumerate(trg_idx) if t==3])/2
    trg_node_pos_signal = trg_node_pos_noise*2 + sum([link_vals[i] for i, t in enumerate(trg_idx) if t==4])/2


    if impostor_sex_col is None:
        x_pos_val = [0.01, 0.6, 1]
        x_pos = [x_pos_val[0], x_pos_val[0], x_pos_val[0], x_pos_val[1], x_pos_val[1]]
        y_pos = [0.01, 0.34, 0.67, trg_node_pos_noise, trg_node_pos_signal]
    else:
        x_pos_val = [0.01, 0.6, 1]
        x_pos = [x_pos_val[0], x_pos_val[0], x_pos_val[0], x_pos_val[0], x_pos_val[0], x_pos_val[1], x_pos_val[1]]
        y_pos = []
        

    # IDENTIFICATION
    if identification_col is not None:
        idn_vals = [0, 1]
        idn_lbls = ['Wrong', 'Correct']
        labels = labels + idn_lbls
        
        if impostor_sex_col is None:
            src_idx = src_idx + [4, 4, 4, 4, 4, 4]
            trg_idx = trg_idx + [5, 6, 5, 6, 5, 6]
                    
    #         idn_link_vals = [((df[trg_col] == 'No') & (df[identification_col] == v)).sum()
    #                          for v in idn_vals]
            idn_link_vals = [((df[trg_col] == 'No') & (df[identification_col] == v) & (df[src_col] == s)).sum()
                             for s in src_vals for v in idn_vals]
        
        else:
            src_idx = src_idx + [6, 6, 6, 6, 6, 6, 6, 6, 6, 6]
            trg_idx = trg_idx + [7, 8, 7, 8, 7, 8, 7, 8, 7, 8]
            idn_link_vals = []
            for s in src_vals:
                for v in idn_vals:
                    if s == 'NONE':
                        idn_link_vals.append(((df[trg_col] == 'No') & (df[identification_col] == v) &
                              (df[src_col] == s)).sum())
                    for sex in src_sex_vals:
                        idn_link_vals.append(((df[trg_col] == 'No') & (df[identification_col] == v) &
                              (df[src_col] == s) & (df[impostor_sex_col] == sex)).sum())
            
#             idn_link_vals = [((df[trg_col] == 'No') & (df[identification_col] == v) &
#                               (df[src_col] == s) & (df[impostor_sex_col] == sex)).sum()
#                              for s in src_vals for v in idn_vals for sex in src_sex_vals]

        
        if percentage:
            idn_link_vals = [v / n_trials_tot for v in idn_link_vals]
            
        link_vals = link_vals + idn_link_vals
        
        for c in range(len(hues)):
            col = f'hsva({hues[c]}, {saturations[c]}, {values[c]-step}, {op})'
            link_cols.append(col)
            col = f'hsva({hues[c]}, {saturations[c]}, {values[c]+step}, {op})'
            link_cols.append(col)
        
#         for c in range(len(hues)):
#             col = f'hsva({hues[c]}, {saturations[c]}, {values[c]+step}, {op})'
#             link_cols.append(col)
            
        col1 = f'hsva({wro_h}, {base_s}, {base_v+step}, {op})'
        col2 = f'hsva({cor_h}, {base_s}, {base_v+step}, {op})'
        
        cols.append(col1)
        cols.append(col2)
        
        if impostor_sex_col is None:
            idn_node_pose = 1 - sum(np.array(link_vals)[np.array(trg_idx)==6]/2)
            not_idn_node_pose = 1 - sum(np.array(link_vals)[np.array(trg_idx)==6]) - sum(np.array(link_vals)[np.array(trg_idx)==5])/2

            x_pos = x_pos + [x_pos_val[2], x_pos_val[2]]
            y_pos = y_pos + [not_idn_node_pose, idn_node_pose]
        else:
            x_pos = []
            y_pos = []
    
#         print(link_vals)
#         print(idn_node_pose)
#         print(not_idn_node_pose)
    
    pad = 5
    
    sank = generate_alluvial(src_idx, trg_idx, link_vals, link_lbls, link_cols, labels, cols, x_pos, y_pos, pad)

    if return_fig:
        return sank
    
    fig = go.Figure(data=[sank])
    fig.update_layout(title_text=title,
                      font_size=15)
    
    columns = ['ACTUAL', 'DETECTION', 'IDENTIFICATION']
    for x, column_name in enumerate(columns):
        fig.add_annotation(
          x=x_pos_val[x],
          y=1.06,
          xref="x",
          yref="paper",
          text=column_name,
          showarrow=False,
          font=dict(
              family="Courier New, monospace",
              size=16,
#               color="tomato"
              ),
          align="center",
          )
        
    fig.update_layout(
      xaxis={
      'showgrid': False, # thin lines in the background
      'zeroline': False, # thick line at x=0
      'visible': False,  # numbers below
      },
      yaxis={
      'showgrid': False, # thin lines in the background
      'zeroline': False, # thick line at x=0
      'visible': False,  # numbers below
      },
        plot_bgcolor='rgba(0,0,0,0)',)

    
    fig.show()
    
    if save_to is not None:
        fig.write_html(save_to)


Overall alluvial plot

In [123]:
plot_alluvial(df=exp_data_imp_adj,
              src_col='condition',
              trg_col='same_room_answer',
              title='Alluvial plot - Overall',
              percentage=True,
              return_fig=False,
              identification_col='impostor_correct_answer',
              impostor_sex_col=None
#               save_to='img_results/alluvial_overall.html'
             )

Analysis per complexity and per room

In [124]:
n_complexities = len(complexities) + 1
n_rooms = len(rooms) + 1
rooms_row_lbl = ['Overall'] + rooms
rooms_lbl = {'Overall': 'Overall', 'LIVING_ROOM': 'Living room', 'METU': 'Classroom', '3D_MARCO': 'Auditorium'}
complexities_col_lbl = ['Overall'] + complexities
fig = make_subplots(rows=n_rooms, cols=n_complexities, start_cell="top-left",
                    specs=[[{"type": "sankey"} for n_c in range(n_complexities)] for n_r in range(n_rooms)],
#                     subplot_titles=[f'Complexity {c} - Room: {r}' for r in rooms_row_lbl for c in complexities],
                    column_titles=[f'Complexity {c}' for c in complexities_col_lbl],
                    row_titles =[f'{rooms_lbl[r]}' for r in rooms_row_lbl],
                   )

for c_idx, complexity in enumerate(complexities_col_lbl):
    
    if c_idx == 0:
#         print(f'OVERALL{complexity}({c_idx}): 1,1')
        fig.add_trace(plot_alluvial(df=exp_data_imp_adj,
                            src_col='condition',
                            trg_col='same_room_answer',
                            title='',
                            percentage=True,
                            return_fig=True,
                            identification_col='impostor_correct_answer',
                            impostor_sex_col=None
                           ),
              row=1,
              col=1
             )
        
        
    else:
        df = exp_data_imp_adj[exp_data_imp_adj['complexity'] == complexity]

#         print(f'ROOMS OVERALL {complexity}({c_idx}): 1,{c_idx+1}')
        fig.add_trace(plot_alluvial(df=df,
                                    src_col='condition',
                                    trg_col='same_room_answer',
                                    title='',
                                    percentage=True,
                                    return_fig=True,
                                    identification_col='impostor_correct_answer'),
                      row=1,
                      col=c_idx+1
                     )
        
    
    for r_idx, room in enumerate(rooms_row_lbl):
        if r_idx == 0:
            continue
        if c_idx == 0:       
            if r_idx+1 != 0:
                df = exp_data_imp_adj[(exp_data_imp_adj['room'] == room)]
#                 print(f'COMPLEXITIES OVERALL {room}({r_idx}): {r_idx+1},1')
                fig.add_trace(plot_alluvial(df=df,
                                            src_col='condition',
                                            trg_col='same_room_answer',
                                            title='',
                                            percentage=True,
                                            return_fig=True,
                                            identification_col='impostor_correct_answer',
                                            impostor_sex_col=None
                                           ),
                             row=r_idx+1,
                             col=1)
                

        else:
            df = exp_data_imp_adj[(exp_data_imp_adj['complexity'] == complexity) & (exp_data_imp_adj['room'] == room)]

#             print(f'ROOM/COMPLEXITY{room}({r_idx}), {complexity}({c_idx}): {r_idx+1},{c_idx+1}')
            fig.add_trace(plot_alluvial(df=df,
                                        src_col='condition',
                                        trg_col='same_room_answer',
                                        title='',
                                        percentage=True,
                                        return_fig=True,
                                        identification_col='impostor_correct_answer'),
                          row=r_idx+1,
                          col=c_idx+1
                         )
            

fig.update_layout(height=1024, width=980, title_text="Alluvial plots per complexity and per room")
fig.show()

# fig.write_html('img_results/alluvial_compl_room.html')

Alluvial plot per gender impostor

In [138]:
exp_data_imp_adj

trial_id  subject_matlab_id  subject_progressive_id  hrtf  complexity  \
0           0                  4                       0    50           3   
1           1                  4                       0    50           3   
2           2                  4                       0    50           3   
3           3                  4                       0    50           3   
4           4                  4                       0    50           3   
..        ...                ...                     ...   ...         ...   
832       832                 32                      30   152           4   
833       833                 32                      30   152           4   
834       834                 32                      30   152           4   
835       835                 32                      30   152           4   
836       836                 32                      30   152           4   

            room condition same_room_answer  same_correct_answer  \
0    LIVING_ROOM  Freeverb               No                    1   
1    LIVING_ROOM   HOA_Bin              Yes                    0   
2    LIVING_ROOM      NONE               No                    0   
3           METU   HOA_Bin               No                    1   
4           METU  Freeverb               No                    1   
..           ...       ...              ...                  ...   
832         METU  Freeverb               No                    1   
833         METU   HOA_Bin               No                    1   
834  LIVING_ROOM      NONE               No                    0   
835  LIVING_ROOM   HOA_Bin               No                    1   
836  LIVING_ROOM  Freeverb               No                    1   

    speaker_impostor  ... position_answer impostor_correct_answer speaker1  \
0              DAVID  ...           MARIA                     0.0    DAVID   
1              MARIA  ...            NONE                     NaN    DAVID   
2               NONE  ...              S5                     0.0    DAVID   
3               ALEX  ...            ALEX                     1.0     ALEX   
4              DAVID  ...           DAVID                     1.0     ALEX   
..               ...  ...             ...                     ...      ...   
832            SUSAN  ...           SUSAN                     1.0    MARIA   
833             ALEX  ...            ALEX                     1.0    SUSAN   
834             NONE  ...              S5                     0.0    SUSAN   
835            SUSAN  ...           DAVID                     0.0    DAVID   
836            DAVID  ...           SUSAN                     0.0     ALEX   

    speaker2  speaker3 speaker4 speaker1_sex speaker2_sex speaker3_sex  \
0      SUSAN     MARIA      NaN            M            F            F   
1      MARIA      ALEX      NaN            M            F            M   
2      SUSAN     MARIA      NaN            M            F            F   
3      DAVID     SUSAN      NaN            M            M            F   
4      SUSAN     DAVID      NaN            M            F            M   
..       ...       ...      ...          ...          ...          ...   
832    SUSAN      ALEX    DAVID            F            F            M   
833    DAVID      ALEX    MARIA            F            M            M   
834    MARIA     DAVID     ALEX            F            F            M   
835    MARIA      ALEX    SUSAN            M            F            M   
836    DAVID     MARIA    SUSAN            M            M            F   

    speaker4_sex  
0            NaN  
1            NaN  
2            NaN  
3            NaN  
4            NaN  
..           ...  
832            M  
833            F  
834            M  
835            F  
836            F  

[837 rows x 23 columns]

In [140]:

plot_alluvial(df=exp_data_imp_adj[exp_data_imp_adj['room']!='LIVING_ROOM'],
              src_col='condition',
              trg_col='same_room_answer',
              title='Impostor sex - Overall',
              percentage=True,
              return_fig=False,
              identification_col=None,#'impostor_correct_answer',
              impostor_sex_col='sex_impostor'
#               save_to='img_results/alluvial_overall.html'
             )

for comp in complexities:
    plot_alluvial(df=exp_data_imp_adj[exp_data_imp_adj['complexity'] == comp],
                  src_col='condition',
                  trg_col='same_room_answer',
                  title=f'Impostor sex - Complexity {comp}',
                  percentage=True,
                  return_fig=False,
                  identification_col=None,#'impostor_correct_answer',
                  impostor_sex_col='sex_impostor'
    #               save_to='img_results/alluvial_overall.html'
                 )


# fig.write_html('img_results/alluvial_compl_impostor_sex.html')

#### Analysis per male/female impostor min/majority - Complexity 2

In [126]:
condition_bin_fv = True

exp_2 = exp_data_imp_adj.copy(deep=True)
exp_2 = exp_2[exp_2['complexity'] == 2]

n_trials_tot = exp_2.shape[0]

identification_col = 'impostor_correct_answer'
src_col = 'condition_sex'
if condition_bin_fv:
    src_val = ['None (MM/FF)', 'None (MF)', 'Bin (MM/FF)', 'Bin (MF)', 'Freeverb (MM/FF)', 'Freeverb (MF)']
else:
    src_val = ['None (MM/FF)', 'None (MF)', 'Signal (MM/FF)', 'Signal (MF)']
trg_col = 'same_room_answer'

labels = src_val+trg_lbl

exp_2[src_col] = pd.Series(dtype='string')
exp_2.loc[(exp_2['condition'] == 'NONE') & (exp_2['speaker1_sex'] == exp_2['speaker2_sex']), src_col] = src_val[0]
exp_2.loc[(exp_2['condition'] == 'NONE') & (exp_2['speaker1_sex'] != exp_2['speaker2_sex']), src_col] = src_val[1]
if condition_bin_fv:
    exp_2.loc[(exp_2['condition'] == 'HOA_Bin') & (exp_2['speaker1_sex'] == exp_2['speaker2_sex']), src_col] = src_val[2]
    exp_2.loc[(exp_2['condition'] == 'HOA_Bin') & (exp_2['speaker1_sex'] != exp_2['speaker2_sex']), src_col] = src_val[3]
    exp_2.loc[(exp_2['condition'] == 'Freeverb') & (exp_2['speaker1_sex'] == exp_2['speaker2_sex']), src_col] = src_val[4]
    exp_2.loc[(exp_2['condition'] == 'Freeverb') & (exp_2['speaker1_sex'] != exp_2['speaker2_sex']), src_col] = src_val[5]
    
    src_idx = [0, 0, 1, 1, 2, 2, 3, 3, 4, 4, 5, 5]
    trg_idx = [6, 7, 6, 7, 6, 7, 6, 7, 6, 7, 6, 7]
    noise_idx = 6
    sig_id = 7
else:
    exp_2.loc[(exp_2['condition'] != 'NONE') & (exp_2['speaker1_sex'] == exp_2['speaker2_sex']), src_col] = src_val[2]
    exp_2.loc[(exp_2['condition'] != 'NONE') & (exp_2['speaker1_sex'] != exp_2['speaker2_sex']), src_col] = src_val[3]
    src_idx = [0, 0, 1, 1, 2, 2, 3, 3]
    trg_idx = [4, 5, 4, 5, 4, 5, 4, 5]
    noise_idx = 4
    sig_id = 5


link_vals = [((exp_2[src_col] == src_val[src_idx[n]]) & (exp_2[trg_col] == trg_val[trg_idx[n] - len(src_val)])).sum()
            for n in range(len(src_idx))]

  
# Compute percentage
link_vals = [v / n_trials_tot for v in link_vals]

# IDENTIFICATION
idn_val = [0, 1]
idn_lbl = ['Wrong', 'Correct']
labels = labels + idn_lbl

if condition_bin_fv:
    src_idx = src_idx + [7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7]
    trg_idx = trg_idx + [8, 9, 8, 9, 8, 9, 8, 9, 8, 9, 8, 9]
    iden_id = 9
    not_iden_id = 8
else:
    src_idx = src_idx + [5, 5, 5, 5, 5, 5, 5, 5]
    trg_idx = trg_idx + [6, 7, 6, 7, 6, 7, 6, 7]
    iden_id = 7
    not_iden_id = 6
    
    
idn_link_vals = [((exp_2[trg_col] == 'No') & (exp_2[identification_col] == v) & (exp_2[src_col] == s)).sum()
                 for s in src_val for v in idn_val]

# Compute percentage
idn_link_vals = [v / n_trials_tot for v in idn_link_vals]
link_vals = link_vals + idn_link_vals

# COLORS
op = 0.35
st = 10
step = 15
if condition_bin_fv:
    hues =        [bin_h, fv_h, bin_h-st, bin_h+st, fv_h-st, fv_h+st,  0,  0,   0,  120]
    saturations = [10,  10, base_s,  base_s, base_s,  base_s,  0,  0,   base_s, base_s]
    values =      [50,  50, base_v,  base_v, base_v,  base_v,  25, 100, base_v, base_v]
        
else:
    hues        = [bin_h, fv_h, bin_h, fv_h, 0,  0,   0,  120]
    saturations = [10,  10, base_s,  base_s, 0,  0,   base_s, base_s]
    values      = [50,  50, base_v,  base_v, 25, 100, base_v, base_v]

cols = []
link_cols = []
for c in range(len(hues)):
    cols.append(f'hsva({hues[c]}, {saturations[c]}, {values[c]+step}, {op})')

for i in range(2):
    for c in range(len(src_val)):
        link_cols.append(f'hsva({hues[c]}, {saturations[c]}, {values[c]-(i*step)}, {op})')
        link_cols.append(f'hsva({hues[c]}, {saturations[c]}, {values[c]}, {op})')
        
        
# POSITION
x_pos_val = [0.01, 0.6, 1]
x_pos = [x_pos_val[0]] * len(src_val) + [x_pos_val[1]] * 2 + [x_pos_val[2]] * 2

trg_node_pos_noise = sum([link_vals[i] for i, t in enumerate(trg_idx) if t==noise_idx])/2
trg_node_pos_signal = trg_node_pos_noise*2 + sum([link_vals[i] for i, t in enumerate(trg_idx) if t==sig_id])/2
idn_node_pose = 1 - sum(np.array(link_vals)[np.array(trg_idx)==iden_id]/2)
not_idn_node_pose = 1 - sum(np.array(link_vals)[np.array(trg_idx)==iden_id]) - sum(np.array(link_vals)[np.array(trg_idx)==not_iden_id])/2

# y_pos = [0.01, 0.34, 0.67, trg_node_pos_noise, trg_node_pos_signal, not_idn_node_pose, idn_node_pose]
y_pos = []
count = 0
for c in src_val:
    perc_c = (exp_2[src_col] == c).sum() / n_trials_tot
    y_pos.append(count + perc_c/2)
    count = count + perc_c
    
y_pos = y_pos + [trg_node_pos_noise, trg_node_pos_signal, not_idn_node_pose, idn_node_pose]

# SANKEY        
sank = generate_alluvial(src_idx, trg_idx, link_vals,
                         link_lbls=[], link_cols=link_cols,
                         labels=labels, cols=cols,
                         x_pos=x_pos, y_pos=y_pos, pad=5)

    
fig = go.Figure(data=[sank])
fig.update_layout(title_text='Alluvial plot by speakers same/different sex - Complexity 2',
                  font_size=15)

columns = ['ACTUAL', 'DETECTION', 'IDENTIFICATION']
for x, column_name in enumerate(columns):
    fig.add_annotation(
      x=x_pos_val[x],
      y=1.06,
      xref="x",
      yref="paper",
      text=column_name,
      showarrow=False,
      font=dict(
          family="Courier New, monospace",
          size=16,
#               color="tomato"
          ),
      align="center",
      )

fig.update_layout(
  xaxis={
  'showgrid': False, # thin lines in the background
  'zeroline': False, # thick line at x=0
  'visible': False,  # numbers below
  },
  yaxis={
  'showgrid': False, # thin lines in the background
  'zeroline': False, # thick line at x=0
  'visible': False,  # numbers below
  },
    plot_bgcolor='rgba(0,0,0,0)',)

fig.show()

#### Analysis per male/female impostor min/majority - Complexity 3

In [127]:
condition_bin_fv = True

exp_3 = exp_data_imp_adj.copy(deep=True)
exp_3 = exp_3[exp_3['complexity'] == 3]

n_trials_tot = exp_3.shape[0]

identification_col = 'impostor_correct_answer'
src_col = 'condition_sex'
if condition_bin_fv:
    src_val = ['None (MMF/MFF)', 'Bin (MMF/MFF->M/F)', 'Bin (MMF/MFF->f/m)', 'Freeverb (MMF/MFF->M/F)', 'Freeverb (MMF/MFF->f/m)']
else:
    src_val = ['None (MMF/MFF)', 'Signal (MMF/MFF->M/F)', 'Signal (MMF/MFF->f/m)']
               
trg_col = 'same_room_answer'

labels = src_val+trg_lbl

exp_3[src_col] = pd.Series(dtype='string')
exp_3.loc[(exp_3['condition'] == 'NONE'), src_col] = src_val[0]
if condition_bin_fv:
    for index, row in exp_3.iterrows():
        if row['condition'] == 'NONE':
            continue
            
        s = row['speaker1_sex'] + row['speaker2_sex'] + row['speaker3_sex']
        n_m = s.count('M')
        n_f = s.count('F')
        maj_imp = ((row['sex_impostor'] == 'M') & (n_m > n_f)) | ((row['sex_impostor'] == 'F') & (n_m < n_f))
        min_imp = ((row['sex_impostor'] == 'M') & (n_m < n_f)) | ((row['sex_impostor'] == 'F') & (n_m > n_f))
        
        if row['condition'] == 'HOA_Bin':
            if maj_imp:
                exp_3.loc[index, src_col] = src_val[1]
            if min_imp:
                exp_3.loc[index, src_col] = src_val[2]
        
        if row['condition'] == 'Freeverb':
            if maj_imp:
                exp_3.loc[index, src_col] = src_val[3]
            if min_imp:
                exp_3.loc[index, src_col] = src_val[4]
            
    src_idx = [0, 0, 1, 1, 2, 2, 3, 3, 4, 4]
    trg_idx = [5, 6, 5, 6, 5, 6, 5, 6, 5, 6]
    noise_idx = 5
    sig_id = 6
else:
    for index, row in exp_3.iterrows():
        if row['condition'] == 'NONE':
            continue
        s = row['speaker1_sex'] + row['speaker2_sex'] + row['speaker3_sex']
        n_m = s.count('M')
        n_f = s.count('F')
        maj_imp = ((row['sex_impostor'] == 'M') & (n_m > n_f)) | ((row['sex_impostor'] == 'F') & (n_m < n_f))
        min_imp = ((row['sex_impostor'] == 'M') & (n_m < n_f)) | ((row['sex_impostor'] == 'F') & (n_m > n_f))

        if maj_imp:
            exp_3.loc[index, src_col] = src_val[1]
        if min_imp:
            exp_3.loc[index, src_col] = src_val[2]
            
    src_idx = [0, 0, 1, 1, 2, 2]
    trg_idx = [3, 4, 3, 4, 3, 4]
    noise_idx = 3
    sig_id = 4


link_vals = [((exp_3[src_col] == src_val[src_idx[n]]) & (exp_3[trg_col] == trg_val[trg_idx[n] - len(src_val)])).sum()
            for n in range(len(src_idx))]

  
# Compute percentage
link_vals = [v / n_trials_tot for v in link_vals]

# IDENTIFICATION
idn_val = [0, 1]
idn_lbl = ['Wrong', 'Correct']
labels = labels + idn_lbl

if condition_bin_fv:
    src_idx = src_idx + [6, 6, 6, 6, 6, 6, 6, 6, 6, 6]
    trg_idx = trg_idx + [7, 8, 7, 8, 7, 8, 7, 8, 7, 8]
    iden_id = 8
    not_iden_id = 7
else:
    src_idx = src_idx + [4, 4, 4, 4, 4, 4]
    trg_idx = trg_idx + [5, 6, 5, 6, 5, 6]
    iden_id = 6
    not_iden_id = 5
    
    
idn_link_vals = [((exp_3[trg_col] == 'No') & (exp_3[identification_col] == v) & (exp_3[src_col] == s)).sum()
                 for s in src_val for v in idn_val]

# Compute percentage
idn_link_vals = [v / n_trials_tot for v in idn_link_vals]
link_vals = link_vals + idn_link_vals

# COLORS
step = 15
st = 10
if condition_bin_fv:
    
    hues =        [0,  bin_h-st, bin_h+st, fv_h-st, fv_h+st, 0,  0,   0,  120]
    saturations = [0,  base_s,       base_s,       base_s,      base_s,      0,  0,   base_s, base_s]
    values =      [25, base_v,       base_v,       base_v,      base_v,      25, 100, base_v, base_v]
        
else:
    hues        = [0,  bin_h, fv_h, 0,  0,   0,  120]
    saturations = [0,  base_s,    base_s,   0,  0,   base_s, base_s]
    values      = [25, base_v,    base_v,   25, 100, base_v, base_v]

cols = []
link_cols = []
for c in range(len(hues)):
    cols.append(f'hsva({hues[c]}, {saturations[c]}, {values[c]+step}, {op})')

for i in range(2):
    for c in range(len(src_val)):
        link_cols.append(f'hsva({hues[c]}, {saturations[c]}, {values[c]-(i*step)}, {op})')
        link_cols.append(f'hsva({hues[c]}, {saturations[c]}, {values[c]}, {op})')
        
        
# POSITION
x_pos_val = [0.01, 0.6, 1]
x_pos = [x_pos_val[0]] * len(src_val) + [x_pos_val[1]] * 2 + [x_pos_val[2]] * 2

trg_node_pos_noise = sum([link_vals[i] for i, t in enumerate(trg_idx) if t==noise_idx])/2
trg_node_pos_signal = trg_node_pos_noise*2 + sum([link_vals[i] for i, t in enumerate(trg_idx) if t==sig_id])/2
idn_node_pose = 1 - sum(np.array(link_vals)[np.array(trg_idx)==iden_id]/2)
not_idn_node_pose = 1 - sum(np.array(link_vals)[np.array(trg_idx)==iden_id]) - sum(np.array(link_vals)[np.array(trg_idx)==not_iden_id])/2

y_pos = []
count = 0
for c in src_val:
    perc_c = (exp_3[src_col] == c).sum() / n_trials_tot
    y_pos.append(count + perc_c/2)
    count = count + perc_c
    
y_pos = y_pos + [trg_node_pos_noise, trg_node_pos_signal, not_idn_node_pose, idn_node_pose]

# SANKEY        
sank = generate_alluvial(src_idx, trg_idx, link_vals,
                         link_lbls=[], link_cols=link_cols,
                         labels=labels, cols=cols,
                         x_pos=x_pos, y_pos=y_pos, pad=5)

    
fig = go.Figure(data=[sank])
fig.update_layout(title_text='Alluvial plot by speakers same/different sex - Complexity 3',
                  font_size=15)

columns = ['ACTUAL', 'DETECTION', 'IDENTIFICATION']
for x, column_name in enumerate(columns):
    fig.add_annotation(
      x=x_pos_val[x],
      y=1.06,
      xref="x",
      yref="paper",
      text=column_name,
      showarrow=False,
      font=dict(
          family="Courier New, monospace",
          size=16,
#               color="tomato"
          ),
      align="center",
      )

fig.update_layout(
  xaxis={
  'showgrid': False, # thin lines in the background
  'zeroline': False, # thick line at x=0
  'visible': False,  # numbers below
  },
  yaxis={
  'showgrid': False, # thin lines in the background
  'zeroline': False, # thick line at x=0
  'visible': False,  # numbers below
  },
    plot_bgcolor='rgba(0,0,0,0)',)

fig.show()

#### Analysis per male/female impostor min/majority - Complexity 4

In [128]:
condition_bin_fv = True

exp_4 = exp_data_imp_adj.copy(deep=True)
exp_4 = exp_4[exp_4['complexity'] == 4]

n_trials_tot = exp_4.shape[0]

identification_col = 'impostor_correct_answer'
src_col = 'condition_sex'
if condition_bin_fv:
    src_val = ['None (MMF/MFF)', 'Bin (MMFF->M)', 'Bin (MMFF->F)', 'Freeverb (MMFF->M)', 'Freeverb (MMFF->F)']
else:
    src_val = ['None (MMF/MFF)', 'Signal (MMFF->M)', 'Signal (MMFF->F)']
               
trg_col = 'same_room_answer'

labels = src_val+trg_lbl

exp_4[src_col] = pd.Series(dtype='string')
exp_4.loc[(exp_4['condition'] == 'NONE'), src_col] = src_val[0]
if condition_bin_fv:
    for index, row in exp_4.iterrows():
        if row['condition'] == 'NONE':
            continue
        
        if row['condition'] == 'HOA_Bin':
            if row['sex_impostor'] == 'M':
                exp_4.loc[index, src_col] = src_val[1]
            if row['sex_impostor'] == 'F':
                exp_4.loc[index, src_col] = src_val[2]
        
        if row['condition'] == 'Freeverb':
            if row['sex_impostor'] == 'M':
                exp_4.loc[index, src_col] = src_val[3]
            if row['sex_impostor'] == 'F':
                exp_4.loc[index, src_col] = src_val[4]
            
    src_idx = [0, 0, 1, 1, 2, 2, 3, 3, 4, 4]
    trg_idx = [5, 6, 5, 6, 5, 6, 5, 6, 5, 6]
    noise_idx = 5
    sig_id = 6
else:
    for index, row in exp_4.iterrows():
        if row['condition'] == 'NONE':
            continue

        if row['sex_impostor'] == 'M':
            exp_4.loc[index, src_col] = src_val[1]
        if row['sex_impostor'] == 'F':
            exp_4.loc[index, src_col] = src_val[2]
            
    src_idx = [0, 0, 1, 1, 2, 2]
    trg_idx = [3, 4, 3, 4, 3, 4]
    noise_idx = 3
    sig_id = 4


link_vals = [((exp_4[src_col] == src_val[src_idx[n]]) & (exp_4[trg_col] == trg_val[trg_idx[n] - len(src_val)])).sum()
            for n in range(len(src_idx))]

  
# Compute percentage
link_vals = [v / n_trials_tot for v in link_vals]

# IDENTIFICATION
idn_val = [0, 1]
idn_lbl = ['Wrong', 'Correct']
labels = labels + idn_lbl

if condition_bin_fv:
    src_idx = src_idx + [6, 6, 6, 6, 6, 6, 6, 6, 6, 6]
    trg_idx = trg_idx + [7, 8, 7, 8, 7, 8, 7, 8, 7, 8]
    iden_id = 8
    not_iden_id = 7
else:
    src_idx = src_idx + [4, 4, 4, 4, 4, 4]
    trg_idx = trg_idx + [5, 6, 5, 6, 5, 6]
    iden_id = 6
    not_iden_id = 5
    
    
idn_link_vals = [((exp_4[trg_col] == 'No') & (exp_4[identification_col] == v) & (exp_4[src_col] == s)).sum()
                 for s in src_val for v in idn_val]

# Compute percentage
idn_link_vals = [v / n_trials_tot for v in idn_link_vals]
link_vals = link_vals + idn_link_vals

# COLORS
step = 15
st = 10
if condition_bin_fv:
    
    hues =        [0,  bin_h-st, bin_h+st, fv_h-st, fv_h+st, 0,  0,   0,  120]
    saturations = [0,  base_s,       base_s,       base_s,      base_s,      0,  0,   base_s, base_s]
    values =      [25, base_v,       base_v,       base_v,      base_v,      25, 100, base_v, base_v]
        
else:
    hues        = [0,  bin_h, fv_h, 0,  0,   0,  120]
    saturations = [0,  base_s,    base_s,   0,  0,   base_s, base_s]
    values      = [25, base_v,    base_v,   25, 100, base_v, base_v]

cols = []
link_cols = []
for c in range(len(hues)):
    cols.append(f'hsva({hues[c]}, {saturations[c]}, {values[c]+step}, {op})')

for i in range(2):
    for c in range(len(src_val)):
        link_cols.append(f'hsva({hues[c]}, {saturations[c]}, {values[c]-(i*step)}, {op})')
        link_cols.append(f'hsva({hues[c]}, {saturations[c]}, {values[c]}, {op})')
        
        
# POSITION
x_pos_val = [0.01, 0.6, 1]
x_pos = [x_pos_val[0]] * len(src_val) + [x_pos_val[1]] * 2 + [x_pos_val[2]] * 2

trg_node_pos_noise = sum([link_vals[i] for i, t in enumerate(trg_idx) if t==noise_idx])/2
trg_node_pos_signal = trg_node_pos_noise*2 + sum([link_vals[i] for i, t in enumerate(trg_idx) if t==sig_id])/2
idn_node_pose = 1 - sum(np.array(link_vals)[np.array(trg_idx)==iden_id]/2)
not_idn_node_pose = 1 - sum(np.array(link_vals)[np.array(trg_idx)==iden_id]) - sum(np.array(link_vals)[np.array(trg_idx)==not_iden_id])/2

y_pos = []
count = 0
for c in src_val:
    perc_c = (exp_4[src_col] == c).sum() / n_trials_tot
    y_pos.append(count + perc_c/2)
    count = count + perc_c
    
y_pos = y_pos + [trg_node_pos_noise, trg_node_pos_signal, not_idn_node_pose, idn_node_pose]

# SANKEY        
sank = generate_alluvial(src_idx, trg_idx, link_vals,
                         link_lbls=[], link_cols=link_cols,
                         labels=labels, cols=cols,
                         x_pos=x_pos, y_pos=y_pos, pad=5)

    
fig = go.Figure(data=[sank])
fig.update_layout(title_text='Alluvial plot by speakers same/different sex - Complexity 4',
                  font_size=15)

columns = ['ACTUAL', 'DETECTION', 'IDENTIFICATION']
for x, column_name in enumerate(columns):
    fig.add_annotation(
      x=x_pos_val[x],
      y=1.06,
      xref="x",
      yref="paper",
      text=column_name,
      showarrow=False,
      font=dict(
          family="Courier New, monospace",
          size=16,
#               color="tomato"
          ),
      align="center",
      )

fig.update_layout(
  xaxis={
  'showgrid': False, # thin lines in the background
  'zeroline': False, # thick line at x=0
  'visible': False,  # numbers below
  },
  yaxis={
  'showgrid': False, # thin lines in the background
  'zeroline': False, # thick line at x=0
  'visible': False,  # numbers below
  },
    plot_bgcolor='rgba(0,0,0,0)',)

fig.show()

### Signal Detection Theory (SDT)

In [129]:
# # hr2, fa2 = pysdt.compute_proportions(((exp_data_sdt['detection_signal_actual']) & (exp_data_sdt['detection_signal_answer'])).sum(),
# src_idx = [0, 0, 1, 1, 2, 2]
#         trg_idx = [3, 4, 3, 4, 3, 4]
#         link_lbls = ['True Negative', 'False Positive', 'False Negative', 'True Positive', 'False Negative', 'True Positive']
#         link_vals = [((df[src_col] == src_vals[src_idx[n]]) & (df[trg_col] == trg_vals[trg_idx[n] - len(src_vals)])).sum()
#                     for n in range(len(src_idx))]#                                    exp_data_sdt['detection_signal_actual'].sum(),
# #                                    ((~exp_data_sdt['detection_signal_actual']) & (exp_data_sdt['detection_signal_answer'])).sum(),
# #                                    (~exp_data_sdt['detection_signal_actual']).sum(),
# #                                    None)
# # print(f'Hit rate: \t\t{hr2*100:.2f}%')
# # print(f'False alarm rate: \t{fa2*100:.2f}%')

# # dprime2 = pysdt.dprime_yes_no(hr, fa)
# # print(f"d': {dprime2:.4f}")

IndentationError: unexpected indent (1806202513.py, line 3)

Compute SDT metrics (sensitivity $d'$, criterion $c$ and likelihood ratio $\beta$) and plots

In [130]:
def get_statistics(sgn_actual, sgn_answer, task, m=None):
    print('\tSUMMARIZING STATISTICS')
    
    hr = ((sgn_actual) & (sgn_answer)).sum() / sgn_actual.sum()
    print(f'\t\tHit rate: \t\t{hr*100:.2f}%')

    fa = ((~sgn_actual) & (sgn_answer)).sum() / (~sgn_actual).sum()
    print(f'\t\tFalse alarm rate: \t{fa*100:.2f}%')
    
    mr = ((sgn_actual) & (~sgn_answer)).sum() / sgn_actual.sum()
    print(f'\t\tMiss rate: \t\t{mr*100:.2f}%')

    cr = ((~sgn_actual) & (~sgn_answer)).sum() / (~sgn_actual).sum()
    print(f'\t\tCorrect rejection rate: {cr*100:.2f}%')
    
    pc = (sgn_actual == sgn_answer).sum() / (sgn_actual).count()
    print(f'\t\tAccuracy p(c): \t\t{pc*100:.2f}%')
    
    print('\n\tSTD METRICS')
    if task == 'detection':
        
        dprime = Z(hr) - Z(fa)

        c = -0.5 * (Z(hr) + Z(fa))

        beta_ln = c*dprime
        beta = math.exp(beta_ln)
        print(f"\t\tbeta: \t\t\t{beta:.4f}")
        print(f"\t\tln(beta): \t\t{beta_ln:.4f}")
    
    elif task == 'identification':
        dprime = pysdt.dprime_mAFC(pc, m)
        
        c = 0
    
    print(f"\t\td': \t\t\t{dprime:.4f}")
    print(f"\t\tc: \t\t\t{c:.4f}")
    
    return dprime, c, hr, fa

def plot_sdt_gaussians(dprime, c, title):
    x=np.linspace(-3, 3, 512)
    noise_dist=norm(-dprime/2,1).pdf(x)
    sgn_dist=norm(dprime/2,1).pdf(x)
    
    fig = go.Figure()
    x_c_idx = min(range(len(x)), key=lambda i: abs(x[i]-c))
    fig.add_trace(go.Scatter(name='True Positives', x=x[x_c_idx:], y=sgn_dist[x_c_idx:], fill='tozeroy', mode='none', fillcolor = 'rgba(204, 155, 209,0.5)'))
    fig.add_trace(go.Scatter(name='False Positives', x=x[x_c_idx:], y=noise_dist[x_c_idx:], fill='tozeroy', mode='none', fillcolor = 'rgba(182, 209, 155,0.5)'))


    fig.add_trace(go.Scatter(name='Noise',x=x, y=noise_dist))
    fig.add_trace(go.Scatter(name='Signal', x=x, y=sgn_dist, line_dash="dash"))

    fig.add_trace(go.Scatter(name='Criterion', x=[c, c], y=[0, np.max(noise_dist)+0.02], line_dash="dot", mode='lines'))
    
    fig.update_layout(title_text=title)
    fig.show()
    
def compute_sdt_metrics(sgn_actual, sgn_answer, task, m=None, sgn_actual2=None, sgn_answer2=None, name='', name2=''):
    print(name)
    dprime, c, hr, fa = get_statistics(sgn_actual, sgn_answer, task)
    
    if (sgn_actual2 is not None) & (sgn_answer2 is not None):
        print(name2)
        dprime2 , c2, hr2, fa2 = get_statistics(sgn_actual2, sgn_answer2, task)
    
    # PLOT ROC
    # sp = np.linspace(-10,10,512)
    # x = norm.cdf(sp-dprime)
    # y = norm.cdf(sp)
    x = np.linspace(0,1,512)
    y = norm.cdf(dprime + Z(x))
    fig = go.Figure()
    fig.add_trace(go.Scatter(name="d'=0", x=[0, 1], y=[0, 1], line_color='#c4c4c4', mode='lines', line=dict(width=1)))
    fig.add_trace(go.Scatter(name="c=0", x=[0, 0.5], y=[1, 0.5], line_dash='dot', line_color='#c4c4c4', mode='lines', line=dict(width=1)))
    fig.add_trace(go.Scatter(name=f"[{name}]d'={dprime:.2f}", x=x, y=y))
    fig.add_trace(go.Scatter(name=f"[{name}]HR={hr:.2f}, FA={fa:.2f}", x=[fa], y=[hr]))

    if (sgn_actual2 is not None) & (sgn_answer2 is not None):
        y = norm.cdf(dprime2 + Z(x))
        fig.add_trace(go.Scatter(name=f"[{name2}]d'={dprime2:.2f}", x=x, y=y))
        fig.add_trace(go.Scatter(name=f"[{name2}]HR={hr2:.2f}, FA={fa2:.2f}", x=[fa2], y=[hr2]))
    
    fig.update_layout(
        title_text=f"ROC",
        yaxis_title_text='Hit Rate',
        xaxis_title_text='False alarm Rate'
    )

    fig.update_xaxes(
        range=[-0.1,1.1],  # sets the range of xaxis
        constrain="domain",  # meanwhile compresses the xaxis by decreasing its "domain"
    )
    fig.update_yaxes(
        range=[-0.1,1.1],  # sets the range of xaxis
        constrain="domain", 
        scaleanchor = "x",
        scaleratio = 1,
      )
    
    fig.show()
    
    # PLOT GAUSSIANS
    plot_sdt_gaussians(dprime, c, title=name)
    
    if (sgn_actual2 is not None) & (sgn_answer2 is not None):
        plot_sdt_gaussians(dprime2, c2, title=name2)

Prepare columns for SDT analysis

In [131]:
exp_data_sdt = exp_data.copy(deep=True)
exp_data_sdt['signal_actual'] = (exp_data_sdt['condition'] == 'HOA_Bin') | (exp_data_sdt['condition'] == 'Freeverb')
exp_data_sdt['detection_signal_answer'] = exp_data_sdt['same_room_answer'] == 'No'
exp_data_sdt['identification_signal_answer'] = exp_data_sdt['speaker_impostor'] == exp_data_sdt['speaker_answer']
df_bin = exp_data_sdt[exp_data_sdt['condition'] != 'Freeverb']
df_fv = exp_data_sdt[exp_data_sdt['condition'] != 'HOA_Bin']

In [132]:
exp_data_sdt

trial_id  subject_matlab_id  subject_progressive_id  hrtf  complexity  \
0           0                  4                       0    50           3   
1           1                  4                       0    50           3   
2           2                  4                       0    50           3   
3           3                  4                       0    50           3   
4           4                  4                       0    50           3   
..        ...                ...                     ...   ...         ...   
832       832                 32                      30   152           4   
833       833                 32                      30   152           4   
834       834                 32                      30   152           4   
835       835                 32                      30   152           4   
836       836                 32                      30   152           4   

            room condition same_room_answer  same_correct_answer  \
0    LIVING_ROOM  Freeverb               No                    1   
1    LIVING_ROOM   HOA_Bin              Yes                    0   
2    LIVING_ROOM      NONE               No                    0   
3           METU   HOA_Bin               No                    1   
4           METU  Freeverb               No                    1   
..           ...       ...              ...                  ...   
832         METU  Freeverb               No                    1   
833         METU   HOA_Bin               No                    1   
834  LIVING_ROOM      NONE               No                    0   
835  LIVING_ROOM   HOA_Bin               No                    1   
836  LIVING_ROOM  Freeverb               No                    1   

    speaker_impostor  ... speaker2 speaker3 speaker4 speaker1_sex  \
0              DAVID  ...    SUSAN    MARIA      NaN            M   
1              MARIA  ...    MARIA     ALEX      NaN            M   
2               NONE  ...    SUSAN    MARIA      NaN            M   
3               ALEX  ...    DAVID    SUSAN      NaN            M   
4              DAVID  ...    SUSAN    DAVID      NaN            M   
..               ...  ...      ...      ...      ...          ...   
832            SUSAN  ...    SUSAN     ALEX    DAVID            F   
833             ALEX  ...    DAVID     ALEX    MARIA            F   
834             NONE  ...    MARIA    DAVID     ALEX            F   
835            SUSAN  ...    MARIA     ALEX    SUSAN            M   
836            DAVID  ...    DAVID    MARIA    SUSAN            M   

     speaker2_sex speaker3_sex speaker4_sex signal_actual  \
0               F            F          NaN          True   
1               F            M          NaN          True   
2               F            F          NaN         False   
3               M            F          NaN          True   
4               F            M          NaN          True   
..            ...          ...          ...           ...   
832             F            M            M          True   
833             M            M            F          True   
834             F            M            M         False   
835             F            M            F          True   
836             M            F            F          True   

    detection_signal_answer identification_signal_answer  
0                      True                        False  
1                     False                        False  
2                      True                        False  
3                      True                        False  
4                      True                        False  
..                      ...                          ...  
832                    True                        False  
833                    True                        False  
834                    True                        False  
835                    True                        False  
836                    True             

#### Detection

Overall

In [133]:
compute_sdt_metrics(df_bin['signal_actual'],
                    df_bin['detection_signal_answer'],
                    task='detection',
                    sgn_actual2=df_fv['signal_actual'],
                    sgn_answer2=df_fv['detection_signal_answer'],
                    name='Bin',
                    name2='Freeverb')

Bin
	SUMMARIZING STATISTICS
		Hit rate: 		54.48%
		False alarm rate: 	43.01%
		Miss rate: 		45.52%
		Correct rejection rate: 56.99%
		Accuracy p(c): 		55.73%

	STD METRICS
		beta: 			1.0092
		ln(beta): 		0.0092
		d': 			0.2886
		c: 			0.0318
Freeverb
	SUMMARIZING STATISTICS
		Hit rate: 		62.01%
		False alarm rate: 	43.01%
		Miss rate: 		37.99%
		Correct rejection rate: 56.99%
		Accuracy p(c): 		59.50%

	STD METRICS
		beta: 			0.9693
		ln(beta): 		-0.0312
		d': 			0.4818
		c: 			-0.0648


Complexity 2

In [134]:
complexity = 2
df_bin2 = df_bin[df_bin['complexity'] == complexity]
df_fv2 = df_fv[df_fv['complexity'] == complexity]

compute_sdt_metrics(df_bin2['signal_actual'],
                    df_bin2['detection_signal_answer'],
                    task='detection',
                    sgn_actual2=df_fv2['signal_actual'],
                    sgn_answer2=df_fv2['detection_signal_answer'],
                    name='Bin',
                    name2='Freeverb')

Bin
	SUMMARIZING STATISTICS
		Hit rate: 		58.06%
		False alarm rate: 	27.96%
		Miss rate: 		41.94%
		Correct rejection rate: 72.04%
		Accuracy p(c): 		65.05%

	STD METRICS
		beta: 			1.1617
		ln(beta): 		0.1499
		d': 			0.7877
		c: 			0.1903
Freeverb
	SUMMARIZING STATISTICS
		Hit rate: 		53.76%
		False alarm rate: 	27.96%
		Miss rate: 		46.24%
		Correct rejection rate: 72.04%
		Accuracy p(c): 		62.90%

	STD METRICS
		beta: 			1.1807
		ln(beta): 		0.1661
		d': 			0.6786
		c: 			0.2448


Complexity 3

In [135]:
complexity = 3
df_bin3 = df_bin[df_bin['complexity'] == complexity]
df_fv3 = df_fv[df_fv['complexity'] == complexity]

compute_sdt_metrics(df_bin3['signal_actual'],
                    df_bin3['detection_signal_answer'],
                    task='detection',
                    sgn_actual2=df_fv3['signal_actual'],
                    sgn_answer2=df_fv3['detection_signal_answer'],
                    name='Bin',
                    name2='Freeverb')

Bin
	SUMMARIZING STATISTICS
		Hit rate: 		50.54%
		False alarm rate: 	46.24%
		Miss rate: 		49.46%
		Correct rejection rate: 53.76%
		Accuracy p(c): 		52.15%

	STD METRICS
		beta: 			1.0044
		ln(beta): 		0.0044
		d': 			0.1080
		c: 			0.0405
Freeverb
	SUMMARIZING STATISTICS
		Hit rate: 		64.52%
		False alarm rate: 	46.24%
		Miss rate: 		35.48%
		Correct rejection rate: 53.76%
		Accuracy p(c): 		59.14%

	STD METRICS
		beta: 			0.9372
		ln(beta): 		-0.0648
		d': 			0.4668
		c: 			-0.1389


Complexity 4

In [136]:
complexity = 4
df_bin4 = df_bin[df_bin['complexity'] == complexity]
df_fv4 = df_fv[df_fv['complexity'] == complexity]

compute_sdt_metrics(df_bin4['signal_actual'],
                    df_bin4['detection_signal_answer'],
                    task='detection',
                    sgn_actual2=df_fv4['signal_actual'],
                    sgn_answer2=df_fv4['detection_signal_answer'],
                    name='Bin',
                    name2='Freeverb')

Bin
	SUMMARIZING STATISTICS
		Hit rate: 		54.84%
		False alarm rate: 	54.84%
		Miss rate: 		45.16%
		Correct rejection rate: 45.16%
		Accuracy p(c): 		50.00%

	STD METRICS
		beta: 			1.0000
		ln(beta): 		-0.0000
		d': 			0.0000
		c: 			-0.1216
Freeverb
	SUMMARIZING STATISTICS
		Hit rate: 		67.74%
		False alarm rate: 	54.84%
		Miss rate: 		32.26%
		Correct rejection rate: 45.16%
		Accuracy p(c): 		56.45%

	STD METRICS
		beta: 			0.9061
		ln(beta): 		-0.0986
		d': 			0.3389
		c: 			-0.2910


#### Identification

Complexity 2

In [137]:
complexity = 2
sgn_actual = exp_data_sdt[exp_data_sdt['complexity'] == complexity]['signal_actual']
sgn_answer = exp_data_sdt[exp_data_sdt['complexity'] == complexity]['identification_signal_answer']

compute_sdt_metrics(sgn_actual, sgn_answer,
                    task='identification',
                    m=complexity)


	SUMMARIZING STATISTICS
		Hit rate: 		0.00%
		False alarm rate: 	72.04%
		Miss rate: 		100.00%
		Correct rejection rate: 27.96%
		Accuracy p(c): 		9.32%

	STD METRICS


TypeError: m must be an int

Complexity 3

In [ ]:
complexity = 3
sgn_actual = exp_data_sdt[exp_data_sdt['complexity'] == complexity]['signal_actual']
sgn_answer = exp_data_sdt[exp_data_sdt['complexity'] == complexity]['identification_signal_answer']

compute_sdt_metrics(sgn_actual, sgn_answer,
                    task='identification',
                    m=complexity)

Complexity 4

In [ ]:
complexity = 4
sgn_actual = exp_data_sdt[exp_data_sdt['complexity'] == complexity]['signal_actual']
sgn_answer = exp_data_sdt[exp_data_sdt['complexity'] == complexity]['identification_signal_answer']

compute_sdt_metrics(sgn_actual, sgn_answer,
                    task='identification',
                    m=complexity)